In [13]:
from pymatgen.core.structure import Structure
from pymatgen.core.structure import IStructure

In [14]:
def get_supercell(file):
    """
    create supercell out of a cif file
    
    return crystal, super_cell
    """
    crystal = Structure.from_file('/home/glard/AML/gnn/GATGNN/DATA/CIF-DATA/%s.cif' % file)
    super_cell = Structure.from_file('/home/glard/AML/gnn/GATGNN/DATA/CIF-DATA/%s.cif' % file)
    scaling_matrix = [[3, 0, 0], [0, 3, 0], [0, 0, 3]]
    super_cell.make_supercell(scaling_matrix=scaling_matrix)
    cd = crystal.as_dict()
    sd = super_cell.as_dict()
#     print(cd.keys())
#     print(cd['lattice'].keys() )
#     print('\n')
#     print(f"lattice-matrix for crystal:   {cd['lattice']['matrix']}")
#     print(f"lattice-matrix for supercell:   {sd['lattice']['matrix']}")
    return crystal, super_cell
  
# crystal, super_cell = get_supercell('mp-19295')

In [15]:
# def dist(file):
#     crystal = Structure.from_file('data/CIF-DATA/%s.cif' % file)
#     super_cell = Structure.from_file('data/CIF-DATA/%s.cif' % file)
#     scaling_matrix = [[3, 0, 0], [0, 3, 0], [0, 0, 3]]
#     super_cell.make_supercell(scaling_matrix=scaling_matrix)
#     cd = crystal.as_dict()
#     print(cd.keys())
#     print(cd['sites'])
#     print(cd['lattice']['matrix'])
#     sd = super_cell.as_dict()
#     #print(cd)
#     #print(sd)
#     shortestDistance = {}
#     #print([i.as_dict()['abc'] for i in super_cell.sites])
#     #print([i.as_dict()['abc'] for i in crystal.sites])
#     center_indices, points_indices, offset_vectors, distances = crystal.get_neighbor_list(r=10)

#     for i, x1 in enumerate(crystal.sites):
#         for j, y1 in enumerate(super_cell.sites):
#             # if i == j or i > j:
#             #     continue
#             # print(x1.specie)
#             x = str(x1.specie)
#             y = str(y1.specie)
#             if not (x, y) in shortestDistance:
#                 shortestDistance[(x, y)] = crystal.distance_matrix[i, j]
#             else:
#                 if crystal.distance_matrix[i, j] < shortestDistance[(x, y)]:
#                     shortestDistance[(x, y)] = crystal.distance_matrix[i, j]
                    
#     # use from_sites as Convenience constructor to make a Molecule from a list of sites.
#     return shortestDistance


# sd = dist('mp-19295')

In [16]:
from pymatgen.core.lattice import Lattice
def get_center(crystal):
    """
    get geo center of a crystal
    return 1 * 3 coord
    """
    center_abc = [0.5, 0.5, 0.5]
    #lat = crystal.lattice()
    sd = crystal.as_dict()
    cart_cords = Lattice(sd['lattice']['matrix']).get_cartesian_coords(center_abc)
    return cart_cords

# center = get_center(super_cell)
# print(center)

In [17]:
def get_100_points(crystal, center_cords):
    """
    get neighbours in a radius of sphere
    return sites, num
    """
    points = crystal.get_sites_in_sphere(center_cords, 10)
    #points = points[:100]
    num = len(points)
    # find nearest site corresponding to the geo center
    # nn = super_cell.get_all_neighbors()
    return points, num
    
# points, num = get_100_points(super_cell, center)
# #print(f"We have found the following sites given r: {points}")
# print(f"We have {num} sites given r")

In [18]:
#from pymatgen.core.sites import distance_from_point
def get_100_nb(crystal, super_cell, center_cords):
    """
    get exactly 100 neighbour sites based on distance matric
    return total_neighbour_num, 100_nearest_sites
    """
    # find nearest site corresponding to the geo center
    shortest_dic = {}
    for s in super_cell:
        shortest_dic[s] = s.distance_from_point(center_cords)
    shortest_dic = sorted(shortest_dic.items(), key=lambda x: x[1], reverse=False)
#     for i in shortest_dic:
#         print(i[0], i[1])
    #return len(crystal.sites), len(super_cell.sites)
    return len(shortest_dic), shortest_dic[:100]
# len_all, sites_list = get_100_nb(crystal, super_cell, center)
# print(len_all, sites_list)

In [19]:
print(sites_list[0])
print(sites_list[0][0])
print(sites_list[0][0].specie)
print(sites_list[0][0].coords)

NameError: name 'sites_list' is not defined

In [20]:
def get_100_cords(sites):
    """
    get element coords for 100 sites:
    format: 100 * 3
    """
    cords = []
    for s in sites:
        cords.append(s[0].coords.tolist())
    return cords

# coords_per_data = get_100_cords(sites_list)
# print(len(coords_per_data), coords_per_data)

In [21]:
import json
def get_100_ele_embedding(sites):
    """
    get element embedding for 100 sites:
    format: 100 * 200
    """
    emb_vector = []
    with open('data/embeddings/matscholar-embedding.json') as json_file:
        embedding = json.load(json_file)

        # Print the type of data variable
#         print("Type:", type(embedding))
#         print("Len:", len(embedding['Be']))

        # Print the data of dictionary
#         print("\nH:", embedding['H'])
#         print("\nBe:", embedding['Be'])
        
        for s in sites:
            emb_vector.append(embedding[s[0].specie.name])
        
    
    return emb_vector
    
# emb_per_data = get_100_ele_embedding(sites_list)
# print(emb_per_data[0])
# print(len(emb_per_data))

In [22]:
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Dense
import numpy as np
from tensorflow.keras.models import Sequential

def get_models():
    """
    get MLP models for element embeddings and coords
    """
    model_ele = Sequential()
    model_ele.add(Input(shape=(200, )))
    model_ele.add(Dense(32, activation="relu"))

    model_cords = Sequential()
    model_cords.add(Input(shape=(3, )))
    model_cords.add(Dense(32, activation="relu"))
    #model.summary()
    # At this point, you can't do this:
    # model.weights

    # You also can't do this:
    # model.summary()

    # Call the model on a test input
    return model_cords, model_ele



In [23]:
def get_trainable_data(emb_per_data, coords_per_data):
    """
    get 100 * 2048 per sample
    """
    model_cords, model_ele = get_models()

    inputs_ele = np.array(emb_per_data)
    ele_32 = model_ele(inputs_ele)
    inputs_cords = np.array(coords_per_data)
    cords_32 = model_cords(inputs_cords)
#     print("Number of weights after calling the model:", len(model_cords.weights))

#     model_ele.summary()
#     model_cords.summary()
#     print(model.weights)
    #print(ele_1024)
    #print(cords_1024)
    latent_vec = np.concatenate((cords_32, ele_32), axis=1)
    #print(latent_vec.shape)
    return latent_vec
    
#latent_vec = get_trainable_data(emb_per_data, coords_per_data)


In [25]:
# without MLP
import os
import sys
import pandas as pd
import numpy as np
def get_data(csv_path, data_dic, num_samples):
    """
    data preprocessing will generate latent vector in .npy files for 2048 CIF files
    each file dimension is 100 * 64
    """
    df = pd.read_csv(csv_path)
    # get {num_samples} items
    i = 0
    err_num = 0
    less4_num = 0
    label_list = []
    id_list = []
    print(os.path)
    for id, label in zip(df['mp-id'], df['band_gap']):
        print(f"Current processing mp-id is {id}, processing: {(i+1)/num_samples}")
        if os.path.exists(data_dic + str(id) + '.npy') is False:
            try:
                crystal, super_cell = get_supercell(id)
            except:
                print("Oops!", sys.exc_info()[0], "occurred.")
                print("Next entry.")
                err_num += 1 
                continue
            if crystal.num_sites < 4:
                less4_num += 1
                continue
            center = get_center(super_cell)
            len_all, sites_list = get_100_nb(crystal, super_cell, center)
            #print(len_all, sites_list)
            coords_per_data = get_100_cords(sites_list)
            emb_per_data = get_100_ele_embedding(sites_list)
            
            
            latent_vec = np.concatenate((coords_per_data, emb_per_data), axis=1)
            print(latent_vec.shape)
            
            np.save(data_dic+str(id) + '.npy', latent_vec)
            id_list.append(id)
            label_list.append(label)
            i += 1
            if i > num_samples - 1:
                print(f"selected {num_sampes} reached")
                break
        else:
            print(f"{id} already exists, continue")
            id_list.append(id)
            label_list.append(label)
            i += 1
            if i > num_samples - 1:
                print(f"selected {num_sampes} reached")
                break
            continue
    
    df = pd.DataFrame(id_list, columns=["mp-id"])
    df["band_gap"] = label_list
    df.to_csv(data_dic + 'band_gap' + str(num_samples) + '.csv', index=False)
    print(f"{num_samples} CIF files have already been processed! Their corresponding .npy files and labeled .csv files are stored under dictionary {data_dic}")
    print(f"cannot find supercell for {err_num} crystals & {less4_num} crystals have less than 4 num_sites")
        
    
get_data('data/properties-reference/bandgap.csv', 'data/processed_data/', 69427)

<module 'posixpath' from '/home/glard/anaconda3/envs/tf_gpu/lib/python3.7/posixpath.py'>
Current processing mp-id is mp-754118, processing: 1.4403618188889048e-05
mp-754118 already exists, continue
Current processing mp-id is mp-978908, processing: 2.8807236377778097e-05
mp-978908 already exists, continue
Current processing mp-id is mp-633688, processing: 4.3210854566667147e-05
mp-633688 already exists, continue
Current processing mp-id is mp-3799, processing: 5.761447275555619e-05
mp-3799 already exists, continue
Current processing mp-id is mp-761650, processing: 7.201809094444524e-05
mp-761650 already exists, continue
Current processing mp-id is mp-12487, processing: 8.642170913333429e-05
mp-12487 already exists, continue
Current processing mp-id is mp-541594, processing: 0.00010082532732222335
mp-541594 already exists, continue
Current processing mp-id is mp-775132, processing: 0.00011522894551111239
mp-775132 already exists, continue
Current processing mp-id is mp-9712, processing:

In [87]:
print(os.path)
if os.path.exists('data/processed_data/mp-633688.npy') is False:
    print('not found mp-633688')
else:
    print('found file mp-633688')
    

<module 'posixpath' from '/home/glard/anaconda3/envs/tf_gpu/lib/python3.7/posixpath.py'>
found file mp-633688


In [13]:
import pandas as pd
import numpy as np
def load_data(data_dic):
    """
    retur all_data and all_label for PCT framework
    """
    df = pd.read_csv(data_dic + 'band_gap4.csv')
    all_data = []
    all_label = []
    for id, label in zip(df['mp-id'], df['band_gap']):
        latent_vec = np.load(data_dic +str(id) +'.npy')
        
        all_data.append(latent_vec)
        all_label.append(label)

#     print(all_label)
    return all_data, all_label

all_data, all_label = load_data('data/processed_data/')
print(all_data[0])
print(np.array(all_data).shape)

[[5.6555862  0.         6.989078   ... 0.         0.         0.        ]
 [4.5105276  0.         6.0015025  ... 0.         0.         0.        ]
 [4.5046425  0.         6.2860827  ... 0.         0.03886996 0.08303429]
 ...
 [2.8831165  0.         3.6106746  ... 0.08270425 0.05540778 0.07032113]
 [6.3171954  0.         8.315767   ... 0.         0.         0.        ]
 [3.8489187  0.         4.674814   ... 0.         0.         0.        ]]
(4, 100, 64)


In [ ]:
# with MLP
import os
import sys
import pandas as pd
def get_data(csv_path, data_dic, num_samples):
    """
    data preprocessing will generate latent vector in .npy files for 2048 CIF files
    each file dimension is 100 * 64
    """
    df = pd.read_csv(csv_path)
    # get {num_samples} items
    i = 0
    label_list = []
    id_list = []
    print(os.path)
    for id, label in zip(df['mp-id'], df['band_gap']):
        print(f"Current processing mp-id is {id}, processing: {(i+1)/num_samples}")
        if os.path.exists(data_dic + str(id) + '.npy') is False:
            try:
                crystal, super_cell = get_supercell(id)
            except:
                print("Oops!", sys.exc_info()[0], "occurred.")
                print("Next entry.")
                continue
            if crystal.num_sites < 4:
                continue
            center = get_center(super_cell)
            len_all, sites_list = get_100_nb(crystal, super_cell, center)
            #print(len_all, sites_list)
            coords_per_data = get_100_cords(sites_list)
            emb_per_data = get_100_ele_embedding(sites_list)
            latent_vec = get_trainable_data(emb_per_data, coords_per_data)
            np.save(data_dic+str(id) + '.npy', latent_vec)
            id_list.append(id)
            label_list.append(label)
            i += 1
            if i > num_samples - 1:
                break
        else:
            print(f"{id} already exists, continue")
            id_list.append(id)
            label_list.append(label)
            i += 1
            continue
    
    df = pd.DataFrame(id_list, columns=["mp-id"])
    df["band_gap"] = label_list
    df.to_csv(data_dic + 'band_gap' + str(num_samples) + '.csv', index=False)
    print(f"{num_samples} CIF files have already been processed! Their corresponding .npy files and labeled .csv files are stored under dictionary {data_dic}")
        
    
get_data('data/properties-reference/bandgap.csv', 'data/processed_data/', 1024)